# Verkehrsszenario_Verhaltensprädiktion

Es soll vorausgesagt werden, ob ein Fahrzeug in einer gegebenen Verkehrssituation das vorausfahrende Fahrzeug überholen wird. Dazu werden der Abstand und die Geschwindigkeit zum vorausfahrenden Fahrzeug gemessen. Zudem wird diese Information von einem Fahrzeug auf der linken Spur gemessen, welches sich von hinten nähert. Als weitere Informationen liegen die jeweiligen Fahrzeugtypen, das Wetter, die Tageszeit und die Straßenart und -krümmung vor.

Mögliche vorherzusagende Reaktionen des Fahrzeugs sind: Geschwindigkeit und Spur beibehalten (continue), Verzögern (decelerate), Spurwechsel bei gleicher Geschwindigkeit (lane change) und Spurwechsel mit Beschleunigung (accelerated lane change).
Entwerfen Sie dazu ein geeignetes Ähnlichkeitsmaß und ermitteln Sie eine Repräsentation des Modells mithilfe von Case Based Learning (Verfahren aus der Vorlesung)

## Aufgabenstellung
Entwickeln Sie eine Software, welche bei Eingabe einer Verkehrssituation (im gleichen Format) die Aktion des Fahrzeugs voraussagen kann. Diskutieren Sie Ihre Konfiguration und das Ergebnis.

## Eingangsdaten
Ein Datensatz von Messungen, in welchem ähnliche Situationen aufgezeichnet wurden -> data/SIM_001.csv

In [6]:
# Imports
from model import *
from similarity import *
import csv

In [7]:
def create_similarity_matrix(filename, key):
    """ 
    Generates similarity matrix 

    Arguments:
        filename: the csv file name as string
        key: the title of the csv which is the value in the first line and col

    Returns:
        similarity dict
    """
    with open(filename) as file:
        similarity_matrix = {}

        for line in csv.DictReader(file, skipinitialspace=True):
            for k, v in line.items():
                if k == key:
                    key_v = v
                    similarity_matrix[key_v] = {}
                else:
                    similarity_matrix[key_v][k] = float(v)

        return similarity_matrix


In [8]:
"""
Read data/SIM_001.csv
"""
case_base_obj = CaseBase.from_csv(
    "data/SIM_001.csv",
    problem_fields = ("v", "v_left", "v_front", "d_left", "d_front", "type_left", "type_front", "radius_curve(m)", "slope_street", "street_type", "time", "weather", "type_vehicle", "speed_limit(km/h)"),
    solution_fields = ("action"),
    encoding = "utf-8",
    delimiter = ";",
    set_int = True
)

In [9]:
"""
Read similarity matrices.
    data/vehicle_type_sim.csv
    data/street_slope_sim.csv
    data/street_type_sim.csv
    data/time_type_sim.csv
    data/weather_type_sim.csv
"""
case_base_obj.add_symbolic_sim(
    field = "type_left",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base_obj.add_symbolic_sim(
    field = "type_front",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base_obj.add_symbolic_sim(
    field = "type_vehicle",
    similarity_matrix = create_similarity_matrix("data/vehicle_type_sim.csv", "type_vehicle")
)

case_base_obj.add_symbolic_sim(
    field = "slope_street",
    similarity_matrix = create_similarity_matrix("data/street_slope_sim.csv", "type_street_slope")
)

case_base_obj.add_symbolic_sim(
    field = "street_type",
    similarity_matrix = create_similarity_matrix("data/street_type_sim.csv", "type_street")
)

case_base_obj.add_symbolic_sim(
    field = "time",
    similarity_matrix = create_similarity_matrix("data/time_type_sim.csv", "type_time")
)

case_base_obj.add_symbolic_sim(
    field = "weather",
    similarity_matrix = create_similarity_matrix("data/weather_type_sim.csv", "type_weather")
)

In [10]:
# Read query from cli
query = Query.from_problems(
    v=28.5,
    v_left=42.5,
    v_front=5,
    d_left=-137,
    d_front=54,
    type_left="motorcycle",
    type_front="truck",
    radius_curve=2391,
    slope_street="flat",
    street_type="country_road (separated)",
    time="day",
    weather="dry",
    type_vehicle="car",
    speed_limit=100,
)

retrieved = case_base_obj.retrieve(
    query,
    v_left=euclid_sim,
    v_front=euclid_sim,
    d_left=euclid_sim,
    d_front=euclid_sim,
    type_left=symbolic_sim,
    type_front=symbolic_sim,
    radius_curve=euclid_sim,
    slope_street=symbolic_sim,
    street_type=symbolic_sim,
    time=symbolic_sim,
    weather=symbolic_sim,
    type_vehicle=symbolic_sim,
    speed_limit=euclid_sim,
)

print("Your Query:")
for k, v in query.problem.items():
    print(f"  - {k} = {v}")
print()


print(f"Prediction: {' ' .join(retrieved.solution.values()).capitalize()}")

# Calculate probability of prediction
prob = 0
count = 0
for field, val in retrieved.sim_per_field.items():
    count += 1
    prob += val

print(f"Probability: {((prob / count) * 100):.2f}%")
print()

print("Explanation:")
for field, val in retrieved.sim_per_field.items():
    print(f"  - {field} =",
          retrieved.problem[field], f"(similarity: {val:.2f})")


Your Query:
  - v = 28.5
  - v_left = 42.5
  - v_front = 5
  - d_left = -137
  - d_front = 54
  - type_left = motorcycle
  - type_front = truck
  - radius_curve = 2391
  - slope_street = flat
  - street_type = country_road (separated)
  - time = day
  - weather = dry
  - type_vehicle = car
  - speed_limit = 100

Prediction: Decelerate
Probability: 92.75%

Explanation:
  - v_left = 42.5 (similarity: 1.00)
  - v_front = 21.5 (similarity: 0.06)
  - d_left = -137.0 (similarity: 1.00)
  - d_front = 54.0 (similarity: 1.00)
  - type_left = motorcycle (similarity: 1.00)
  - type_front = truck (similarity: 1.00)
  - radius_curve(m) = 2391.0 (similarity: 1.00)
  - slope_street = flat (similarity: 1.00)
  - street_type = country_road (separated) (similarity: 1.00)
  - time = day (similarity: 1.00)
  - weather = dry (similarity: 1.00)
  - type_vehicle = car (similarity: 1.00)
  - speed_limit(km/h) = 100.0 (similarity: 1.00)


## Entwurf und Umsetzung

Allgemein ist ein Case-Based Reasoning (CBR) Algorithmus eine Methode des maschinellen Lernens, bei der Probleme durch den Vergleich mit früheren, ähnlichen Fällen gelöst werden. Ein CBR-System arbeitet, indem es die Merkmale des aktuellen Problems mit gespeicherten Fällen vergleicht und auf Basis dieser Vergleiche eine Lösung vorschlägt. Dadurch kann der Algorithmus in einer Vielzahl von Anwendungsbereichen, die auch einen hohen Grad an Expertise erfordern können, zum Einsatz kommen. 

Beim Entwurf des Algorithmus wird darauf geachtet dass dieser auch einfach auf andere Problemstellungen angepasst werden kann. Darüber hinaus wird die Lösung in der Sprache Python umgesetzt werden.

![Alt-Text](./KI.png "Entwurf des Algorithmus")

Wie in der obigen Abbildung zu erkennen, wird der Algorithmus in drei Bereiche unterteilt. Dies ist erstens das Notebook, dadurch kann der Nutzer komfortabel auf die von ihm benötigten Funktionen zurückgreifen. Die Funktionalität wird über die model.py und die similarity.py bereitgestellt. Dabei ist die model.py das eigentliche Modell, welches über das Laden der CSV Dateien kalibriert wird. In der similarity.py befinden sich die Algorithmen, die für den Vergleich der Eingabeparameter benötigt werden.


## Diskussion der Konfiguration

Wie bereits unter dem Punkt "Entwurf und Umsetzung" erwähnt, wird das Modell in diesem Fall über CSV Dateien kalibriert. Einerseits werden die generellen Datensätze geladen, die sich in der SIM_001.csv befinden, aber auch die Ähnlichkeitsmatrizen. Erst durch diese Ähnlichkeitsmatrizen wird dem Modell ermöglicht, die in Textform, zur Verfügung stehenden Features im Datensatz zu interpretieren und auch sicher auf andere Situationen anzuwenden. Denn durch diese wird der Zusammenhang der verschiedenen Auftrittsmöglichkeiten festgelegt. 

Festgelegt werden müssen in diesem Anwendungsfall die Beziehung zwischen den verschiedenen Straßenneigungen (flat, ascending, decending), des Straßentyps (country_road (separated),   autobahn), des Zeittyps (night, dusk, day, dawn), des Fahrzeugtyps (car, motorcycle, sportscar, truck) und der Wetterart (dry, rain, fog, snow_ice).

Die Erstellung der Ähnlichkeitsmatrix für die Straßenneigung wird nun im Folgenden näher erläutert:

| type_street_slope | flat | ascending | decending |
| ----| ----| ----| ----|
| <b>flat</b> | 1.0 | 0.3 | 0.7 |
| <b>ascending</b> | 0.3 | 1.0 | 0.1 |
| <b>decending</b> | 0.7 | 0.1 | 1.0 |

Das Ähnlichkeitsmaß ist eine Zahl zwischen null und eins, wobei null das Gegenteil und eins das gleiche wieder spiegelt. Wie zu erkennen ist, befindet sich in der Diagonale an jeder Stelle eine eins. Dies ist der Fall, da flat mit flat verglichen komplett gleich ist. Nun könnte man annehmen, dass bei den möglichen Zuständen flach, aufsteigend und absteigend der Vergleich zwischen flach und aufsteigend mit 0.5 bewertet wird. Wie in der Matrix zu erkennen, beträgt er jedoch 0.3. Denn die Bewertung muss im Kontext des Anwendungsfalls erfolgen, auf einer aufsteigenden Straße zu überholen ist deutlich risikoreicher als auf einer flachen oder sogar absteigenden Straße. Es ist damit zu rechnen, dass auf einer aufsteigenden Straße die Beschleunigung länger dauert, gleichzeitig rollt der Gegenverkehr den Berg herunter und fährt dadurch eventuell auch etwas zu schnell, da er weniger Widerstand hat. Dadurch ergibt sich eine Ähnlichkeit von 0.3. Eine flache zu einer absteigenden Straße haben wir mit 0.7 bewertet. Mit der Begründung, dass ein Überholvorgang auf einer flachen und einer absteigenden Straße ein ähnlich hohes Risiko mit sich bringt. Auf die Beschreibung des Vergleiches der restlichen Werte wird an dieser Stelle verzichtet, da sich das Vorgehen nur wiederholen würde.

## Diskussion des Ergbenisses

Durch die Aufteilung des Datensatzes (SIM_001.csv) in Trainings- und Testdaten kann die einwandfreie Funktion des Algorithmus sichergestellt werden. Denn das zu erwartende Ergebnis ist bei der Eingabe der dazugehörenden Parameter bereits bekannt. Bei den Tests des Algorithmus wurden alle Testcases richtig vorhergesagt. Dadurch kann von einer guten Genauigkeit des Algorithmus ausgegangen werden. 

Zusammenfassend vereinen Case-Based Reasoning (CBR) Algorithmen einige große Vorteile, die auch in diesem Anwendungsfall zum Vorschein getreten sind. Dazu gehört beispielsweise die Möglichkeit auch komplexe Probleme wie die Entscheidung eines Überholvorgang durch den Vergleich mit ähnlichen Fällen aus der Vergangenheit lösen zu können. Dadurch wird aber auch einer der Nachteile eines solchen Algorithmus deutlich, die Qualität hängt von der Güte und der Menge an zur Verfügung stehenden Daten ab. Auffallend ist, dass der Algorithmus sehr anpassbar und schnell an spezifische Anforderungen und Umstände angepasst werden kann. 